## Overview

This notebook will show you how to create and query a table or DataFrame that you uploaded to DBFS. [DBFS](https://docs.databricks.com/user-guide/dbfs-databricks-file-system.html) is a Databricks File System that allows you to store data for querying inside of Databricks. This notebook assumes that you have a file already inside of DBFS that you would like to read from.

This notebook is written in **Python** so the default cell type is Python. However, you can use different languages by using the `%LANGUAGE` syntax. Python, Scala, SQL, and R are all supported.

In [2]:
dbutils.library.installPyPI("mlflow")
dbutils.library.restartPython()
import mlflow

Sun Jul 19 19:58:53 2020 py4j imported

In [3]:
from pyspark.sql.functions import isnan, when, count, col

from pyspark.sql import functions as F 
from pyspark.sql import Window

In [4]:
# File location and type
file_location = "/FileStore/tables/RS_v2_2006_03"
file_type = "json"

# CSV options
infer_schema = "false"
first_row_is_header = "false"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df_train = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df_train)

archived author author_cakeday author_flair_background_color author_flair_css_class author_flair_richtext author_flair_text author_flair_text_color author_flair_type brand_safe can_gild contest_mode created_utc distinguished domain edited gilded hidden hide_score id is_crosspostable is_reddit_media_domain is_self is_video link_flair_css_class link_flair_richtext link_flair_text link_flair_text_color link_flair_type locked media no_follow num_comments num_crossposts over_18 parent_whitelist_status permalink post_hint preview retrieved_on rte_mode score secure_media selftext send_replies spoiler stickied subreddit subreddit_id subreddit_name_prefixed subreddit_type suggested_sort thumbnail thumbnail_height thumbnail_width title url whitelist_status true codepoet null null null List() null null text true true false 1141171234 null macgeekery.com false 0 false false 2icw true false false false null List() null dark text false null true 0 0 false all_ads /r/reddit.com/comments/2icw/well_that_was_a_bust/ null null null markdown 0 null true false false reddit.com t5_6 r/reddit.com archived null default null null Well That Was a Bust http://www.macgeekery.com/opinion/well_that_was_a_bust all_ads true scylla null null null List() null null text true true false 1141171723 null msnbc.msn.com false 0 false false 2idn true false false false null List() null dark text false null true 0 0 false all_ads /r/reddit.com/comments/2idn/holocaust_why_david_irving_shouldnt_be_jailed_and/ null null null markdown 0 null true false false reddit.com t5_6 r/reddit.com archived null default null null Holocaust: Why David Irving shouldn’t be jailed ( and it's not because he's in any ways right ) http://www.msnbc.msn.com/id/11569497/site/newsweek/ all_ads true tilto null null null List() null null text true true false 1141171939 null iht.com false 0 false false 2ie4 true false false false null List() null dark text false null true 0 0 false all_ads /r/reddit.com/comments/2ie4/google_shares_fall_sharply_as_cfo_announces/ null null null markdown 0 null true false false reddit.com t5_6 r/reddit.com archived null default null null Google shares fall sharply as CFO announces growth is slowing http://www.iht.com/articles/2006/02/28/business/google.php all_ads true Laibcoms null null null List() null null text true true false 1141172196 null gameshogun.info false 0 false false 2iek true false false false null List() null dark text false null true 0 0 false all_ads /r/reddit.com/comments/2iek/newsvine_launching_tomorrow/ null null null markdown 0 null true false false reddit.com t5_6 r/reddit.com archived null default null null newsvine launching tomorrow! http://gameshogun.info/index.php/Tech/2006/03/01/newsvine_launching_tomorrow all_ads true FaeLLe null null null List() null null text true true false 1141172277 null faelle.com false 0 false false 2ies true false false false null List() null dark text false null true 0 0 false all_ads /r/reddit.com/comments/2ies/voodoopc_to_launch_8tb_media_pc/ null null null markdown 0 null true false false reddit.com t5_6 r/reddit.com archived null default null null VoodooPC to launch 8TB Media PC http://www.FaeLLe.com/2006/03/voodoopc-plans-8tb-media-pc.html all_ads true Megasphaera null null null List() null null text true true false 1141172696 null request.reddit.com false 0 false false 2if8 true false false false null List() null dark text false null true 1 0 false all_ads /r/reddit.com/comments/2if8/kafka_immigration/ null null null markdown 0 null true false false reddit.com t5_6 r/reddit.com archived null default null null kafka immigration http://request.reddit.com/goto?id=2i9k all_ads true alsaad null null null List() null null text false true false 1141173165 null pandora.com false 0 false false 2ig1 false false false false null List() null dark text false null true 0 0 false null /r/pl/comments/2ig1/pandoracom_wybieraj_oceniaj_i_sluchaj_tego_co/ null null null markdown 4 null true false false pl t5_2475 r/pl restrict

In [5]:
len(df_train.columns)

Out[3]: 58

In [6]:
columns_to_drop = ['archived', 'author_cakeday', 'author_flair_text_color', 'author_flair_background_color', 'author_flair_css_class', \
                   'author_flair_richtext', 'author_flair_text', 'author_flair_type', 'contest_mode', 'edited', 'gilded', 'hidden', 'hide_score', \
                   'is_reddit_media_domain', 'is_self', 'is_video', 'distinguished', 'link_flair_css_class', 'link_flair_richtext', \
                   'link_flair_text', 'post_hint', 'link_flair_text_color', 'link_flair_type', 'locked', 'media', 'rte_mode', 'preview', \
                   'retrieved_on', 'secure_media', 'selftext', 'send_replies', 'spoiler', 'stickied', 'thumbnail', 'thumbnail_height', \
                   'thumbnail_width', 'whitelist_status', 'num_crossposts', 'suggested_sort']

df_train = df_train.drop(*columns_to_drop)

In [7]:
display(df_train)

author brand_safe can_gild created_utc domain id is_crosspostable no_follow num_comments over_18 parent_whitelist_status permalink score subreddit subreddit_id subreddit_name_prefixed subreddit_type title url codepoet true true 1141171234 macgeekery.com 2icw true true 0 false all_ads /r/reddit.com/comments/2icw/well_that_was_a_bust/ 0 reddit.com t5_6 r/reddit.com archived Well That Was a Bust http://www.macgeekery.com/opinion/well_that_was_a_bust scylla true true 1141171723 msnbc.msn.com 2idn true true 0 false all_ads /r/reddit.com/comments/2idn/holocaust_why_david_irving_shouldnt_be_jailed_and/ 0 reddit.com t5_6 r/reddit.com archived Holocaust: Why David Irving shouldn’t be jailed ( and it's not because he's in any ways right ) http://www.msnbc.msn.com/id/11569497/site/newsweek/ tilto true true 1141171939 iht.com 2ie4 true true 0 false all_ads /r/reddit.com/comments/2ie4/google_shares_fall_sharply_as_cfo_announces/ 0 reddit.com t5_6 r/reddit.com archived Google shares fall sharply as CFO announces growth is slowing http://www.iht.com/articles/2006/02/28/business/google.php Laibcoms true true 1141172196 gameshogun.info 2iek true true 0 false all_ads /r/reddit.com/comments/2iek/newsvine_launching_tomorrow/ 0 reddit.com t5_6 r/reddit.com archived newsvine launching tomorrow! http://gameshogun.info/index.php/Tech/2006/03/01/newsvine_launching_tomorrow FaeLLe true true 1141172277 faelle.com 2ies true true 0 false all_ads /r/reddit.com/comments/2ies/voodoopc_to_launch_8tb_media_pc/ 0 reddit.com t5_6 r/reddit.com archived VoodooPC to launch 8TB Media PC http://www.FaeLLe.com/2006/03/voodoopc-plans-8tb-media-pc.html Megasphaera true true 1141172696 request.reddit.com 2if8 true true 1 false all_ads /r/reddit.com/comments/2if8/kafka_immigration/ 0 reddit.com t5_6 r/reddit.com archived kafka immigration http://request.reddit.com/goto?id=2i9k alsaad false true 1141173165 pandora.com 2ig1 false true 0 false null /r/pl/comments/2ig1/pandoracom_wybieraj_oceniaj_i_sluchaj_tego_co/ 4 pl t5_2475 r/pl restricted Pandora.com - wybieraj, oceniaj i sluchaj tego co lubisz. Za free. http://pandora.com/ Megasphaera true true 1141173275 rxpgnews.com 2ig8 true true 0 false all_ads /r/reddit.com/comments/2ig8/meditation_changes_brain_structure/ 0 reddit.com t5_6 r/reddit.com archived meditation changes brain structure http://www.rxpgnews.com/research/neurosciences/article_2837.shtml benm true true 1141173366 blogs.pragprog.com 2igf true true 0 false all_ads /r/programming/comments/2igf/annotate_models_plugin_for_rails/ 7 programming t5_2fwo r/programming public Annotate Models Plugin for Rails http://blogs.pragprog.com/cgi-bin/pragdave.cgi/Tech/Ruby/AnnotateModels.rdoc johnny_yuma true true 1141173368 cbsnews.com 2igg true false 1 false all_ads /r/reddit.com/comments/2igg/kids_build_soybeanfueled_car/ 9 reddit.com t5_6 r/reddit.com archived Kids Build Soybean-Fueled Car http://www.cbsnews.com/stories/2006/02/17/eveningnews/main1329941.shtml trost true true 1141173632 austin360.com 2ihd true false 2 false all_ads /r/reddit.com/comments/2ihd/bah_hummer_indie_rockers_reject_big_money_from/ 39 reddit.com t5_6 r/reddit.com archived Bah Hummer: Indie rockers reject big money from the king of gas guzzlers http://www.austin360.com/music/content/music/stories/2006/02/22hummer.html iwadon false true 1141174155 x.nest.jp 2ihu true true 1 false null /r/ja/comments/2ihu/life_with_mac_os_x_rnote_ical化けてませんか/ 0 ja t5_22i6 r/ja public Life with Mac OS X @rNote - iCal、化けてませんか？ http://x.nest.jp/mac/060204_0015.htm honekaimedia true true 1141174299 techeblog.com 2ii3 true false 0 false all_ads /r/reddit.com/comments/2ii3/what_if_microsoft_designed_the_ipods_packaging/ 1 reddit.com t5_6 r/reddit.com archived What if Microsoft Designed the iPod’s Packaging? http://www.techeblog.com/index.php/tech-gadget/what-if-microsoft-designed-the-ipods-packaging dr2tom true true 1141175199 nightwithafuturist.com 2ij8 false true 1 false all_ads /r/reddit.com/comments/2ij8/future_of_bioen

In [8]:
len(df_train.columns)

Out[6]: 19

In [9]:
# File location and type
file_location = "/FileStore/tables/RS_v2_2006_04-1"
file_type = "json"

# CSV options
infer_schema = "false"
first_row_is_header = "false"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df_test = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df_test)

archived author author_cakeday author_flair_background_color author_flair_css_class author_flair_richtext author_flair_text author_flair_text_color author_flair_type brand_safe can_gild contest_mode created_utc distinguished domain edited gilded hidden hide_score id is_crosspostable is_reddit_media_domain is_self is_video link_flair_css_class link_flair_richtext link_flair_text link_flair_text_color link_flair_type locked media no_follow num_comments num_crossposts over_18 parent_whitelist_status permalink post_hint preview retrieved_on rte_mode score secure_media selftext send_replies spoiler stickied subreddit subreddit_id subreddit_name_prefixed subreddit_type suggested_sort thumbnail thumbnail_height thumbnail_width title url whitelist_status true spif null null null List() null null text true true false 1143849794 null democrats.reform.house.gov false 0 false false 3rip true false false false null List() null dark text false null false 0 0 false all_ads /r/reddit.com/comments/3rip/iraq_on_the_record_a_searchable_collection_of_237/ null null null markdown 4 null true false false reddit.com t5_6 r/reddit.com archived null default null null Iraq on the Record: A Searchable Collection Of 237 Specific Misleading Statements Made By Bush Administration Officials About The Threat Posed By Iraq http://democrats.reform.house.gov/IraqOnTheRecord/ all_ads true jjzak null null null List() null null text false true false 1143849822 null rubricks.org false 0 false false 3rir true false false false null List() null dark text false null false 0 0 false null /r/ja/comments/3rir/rubricks_cms_on_rails/ null null null markdown 3 null true false false ja t5_22i6 r/ja public new default null null Rubricks - CMS on Rails http://rubricks.org/ null true toddieg null null null List() null null text true true false 1143849849 null randomcraponline.com false 0 false false 3ris false false false false null List() null dark text false null true 1 0 false all_ads /r/reddit.com/comments/3ris/islamic_dance_party/ null null null markdown 0 null true false false reddit.com t5_6 r/reddit.com archived null default null null Islamic Dance Party http://www.randomcraponline.com/islamic-dance-party/ all_ads true rmc null null null List() null null text true true false 1143849910 null debian-administration.org false 0 false false 3riv true false false false null List() null dark text false null false 1 0 false all_ads /r/reddit.com/comments/3riv/how_to_make_bash_complete_differently_based_on/ null null null markdown 3 null true false false reddit.com t5_6 r/reddit.com archived null default null null How to make bash complete differently based on the command. http://www.debian-administration.org/articles/317 all_ads true toddieg null null null List() null null text false true false 1143850224 null randomcraponline.com false 0 false false 3rj0 false false false false null List() null dark text false null true 0 0 true promo_adult_nsfw /r/nsfw/comments/3rj0/hot_web_cam_chicks/ null null null markdown 0 null true false false nsfw t5_vf2 r/nsfw public null default null null Hot Web Cam Chicks http://www.randomcraponline.com/web-cam-chicks/?bikini-thong/ promo_adult_nsfw true tiagocardoso null null null List() null null text true true false 1143850300 null mainada.net false 0 false false 3rj3 true false false false null List() null dark text false null true 0 0 false all_ads /r/reddit.com/comments/3rj3/manga_style_other_sketches_see_the_artist_creation/ null null null markdown 0 null true false false reddit.com t5_6 r/reddit.com archived null default null null Manga Style & other sketches - see the artist creation http://www.mainada.net/comics/index/mangastyle all_ads true neotrantor null null null List() null null text true true false 1143850524 null blog.cognitivelabs.com false 0 false false 3rj5 true false false false null List() null dark text false null true 0 0 false all_ads /r/reddit.com/comments/3rj5/scent_of_fear_improves_cognitive_performance_in/ null null nul

In [10]:
len(df_test.columns)

Out[8]: 58

In [11]:
# df.drop('author_cakeday').collect()

columns_to_drop = ['archived', 'author_cakeday', 'author_flair_text_color', 'author_flair_background_color', 'author_flair_css_class', \
                   'author_flair_richtext', 'author_flair_text', 'author_flair_type', 'contest_mode', 'edited', 'gilded', 'hidden', 'hide_score', \
                   'is_reddit_media_domain', 'is_self', 'is_video', 'distinguished', 'link_flair_css_class', 'link_flair_richtext', \
                   'link_flair_text', 'post_hint', 'link_flair_text_color', 'link_flair_type', 'locked', 'media', 'rte_mode', 'preview', \
                   'retrieved_on', 'secure_media', 'selftext', 'send_replies', 'spoiler', 'stickied', 'thumbnail', 'thumbnail_height', \
                   'thumbnail_width', 'whitelist_status', 'num_crossposts', 'suggested_sort']

df_test = df_test.drop(*columns_to_drop)

In [12]:
display(df_test)

author brand_safe can_gild created_utc domain id is_crosspostable no_follow num_comments over_18 parent_whitelist_status permalink score subreddit subreddit_id subreddit_name_prefixed subreddit_type title url spif true true 1143849794 democrats.reform.house.gov 3rip true false 0 false all_ads /r/reddit.com/comments/3rip/iraq_on_the_record_a_searchable_collection_of_237/ 4 reddit.com t5_6 r/reddit.com archived Iraq on the Record: A Searchable Collection Of 237 Specific Misleading Statements Made By Bush Administration Officials About The Threat Posed By Iraq http://democrats.reform.house.gov/IraqOnTheRecord/ jjzak false true 1143849822 rubricks.org 3rir true false 0 false null /r/ja/comments/3rir/rubricks_cms_on_rails/ 3 ja t5_22i6 r/ja public Rubricks - CMS on Rails http://rubricks.org/ toddieg true true 1143849849 randomcraponline.com 3ris false true 1 false all_ads /r/reddit.com/comments/3ris/islamic_dance_party/ 0 reddit.com t5_6 r/reddit.com archived Islamic Dance Party http://www.randomcraponline.com/islamic-dance-party/ rmc true true 1143849910 debian-administration.org 3riv true false 1 false all_ads /r/reddit.com/comments/3riv/how_to_make_bash_complete_differently_based_on/ 3 reddit.com t5_6 r/reddit.com archived How to make bash complete differently based on the command. http://www.debian-administration.org/articles/317 toddieg false true 1143850224 randomcraponline.com 3rj0 false true 0 true promo_adult_nsfw /r/nsfw/comments/3rj0/hot_web_cam_chicks/ 0 nsfw t5_vf2 r/nsfw public Hot Web Cam Chicks http://www.randomcraponline.com/web-cam-chicks/?bikini-thong/ tiagocardoso true true 1143850300 mainada.net 3rj3 true true 0 false all_ads /r/reddit.com/comments/3rj3/manga_style_other_sketches_see_the_artist_creation/ 0 reddit.com t5_6 r/reddit.com archived Manga Style & other sketches - see the artist creation http://www.mainada.net/comics/index/mangastyle neotrantor true true 1143850524 blog.cognitivelabs.com 3rj5 true true 0 false all_ads /r/reddit.com/comments/3rj5/scent_of_fear_improves_cognitive_performance_in/ 0 reddit.com t5_6 r/reddit.com archived Scent of Fear Improves Cognitive Performance in Women http://blog.cognitivelabs.com/2006/03/scent-of-fear-improves-cognitive.html honekaimedia true true 1143850569 techeblog.com 3rj6 true true 1 false all_ads /r/reddit.com/comments/3rj6/top_10_strangest_cell_phones/ 0 reddit.com t5_6 r/reddit.com archived Top 10 Strangest Cell Phones http://www.techeblog.com/index.php/tech-gadget/top-10-strangest-cell-phones eglobe1 true true 1143850981 eglobe1.com 3rja false true 0 false all_ads /r/reddit.com/comments/3rja/ten_crazy_usb/ 0 reddit.com t5_6 r/reddit.com archived ten crazy usb http://www.eglobe1.com/index.php/2006/03/31/10-crazy-usb/ otsune false true 1143851173 bsddiary.net 3rjc true true 0 false null /r/ja/comments/3rjc/bind9_設定/ 3 ja t5_22i6 r/ja public bind9 設定 http://www.bsddiary.net/doc/bind9.html quicklybored true true 1143851249 quicklybored.com 3rjh true true 1 false all_ads /r/reddit.com/comments/3rjh/the_greatest_blackberry_game_of_all_time_reviewed/ 0 reddit.com t5_6 r/reddit.com archived The greatest BlackBerry game of all time reviewed http://www.quicklybored.com/index.cfm/2006/3/30/Tron#more gamergoal true true 1143851327 mugshots.com 3rjk true true 0 false all_ads /r/reddit.com/comments/3rjk/beavis_is_alive_and_well/ 1 reddit.com t5_6 r/reddit.com archived Beavis is alive and well http://www.mugshots.com/Favorites/Chris+Kemp.htm spif true true 1143852520 bedtime-story.com 3rk7 true false 0 false all_ads /r/reddit.com/comments/3rk7/the_history_of_alice_in_wonderland/ 6 reddit.com t5_6 r/reddit.com archived The History Of Alice In Wonderland http://www.bedtime-story.com/bedtime-story/alice-background.htm kwsdurango true true 1143853144 kurtschmidt.com 3rkc true true 0 false all_ads /r/reddit.com/comments/3rkc/emerging_uk_rockers_66_now_on_itunes/ 0 reddit.com t5_6 r/reddit.com archived Emerging UK Rockers "66" now on i-Tunes! http://kurtschmidt.com/comments.php

In [13]:
len(df_test.columns)

Out[11]: 19

In [14]:
df_train = df_train.fillna( {'parent_whitelist_status':'no_status'} )
df_test = df_test.fillna( {'parent_whitelist_status':'no_status'} )

In [15]:
display(df_train.select([count(when(col(c).isNull(), c)).alias(c) for c in df_train.columns]))

author brand_safe can_gild created_utc domain id is_crosspostable no_follow num_comments over_18 parent_whitelist_status permalink score subreddit subreddit_id subreddit_name_prefixed subreddit_type title url 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

In [16]:
display(df_test.select([count(when(col(c).isNull(), c)).alias(c) for c in df_test.columns]))

author brand_safe can_gild created_utc domain id is_crosspostable no_follow num_comments over_18 parent_whitelist_status permalink score subreddit subreddit_id subreddit_name_prefixed subreddit_type title url 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

In [17]:
columns_to_drop2 = ['created_utc', 'id', 'permalink', 'subreddit_id', 'subreddit_name_prefixed', 'url']

df_train = df_train.drop(*columns_to_drop2)

In [18]:
len(df_train.columns)

Out[16]: 13

In [19]:
columns_to_drop2 = ['created_utc', 'id', 'permalink', 'subreddit_id', 'subreddit_name_prefixed', 'url']

df_test = df_test.drop(*columns_to_drop2)

In [20]:
len(df_test.columns)

Out[18]: 13

In [21]:
display(df_train)

author brand_safe can_gild domain is_crosspostable no_follow num_comments over_18 parent_whitelist_status score subreddit subreddit_type title codepoet true true macgeekery.com true true 0 false all_ads 0 reddit.com archived Well That Was a Bust scylla true true msnbc.msn.com true true 0 false all_ads 0 reddit.com archived Holocaust: Why David Irving shouldn’t be jailed ( and it's not because he's in any ways right ) tilto true true iht.com true true 0 false all_ads 0 reddit.com archived Google shares fall sharply as CFO announces growth is slowing Laibcoms true true gameshogun.info true true 0 false all_ads 0 reddit.com archived newsvine launching tomorrow! FaeLLe true true faelle.com true true 0 false all_ads 0 reddit.com archived VoodooPC to launch 8TB Media PC Megasphaera true true request.reddit.com true true 1 false all_ads 0 reddit.com archived kafka immigration alsaad false true pandora.com false true 0 false no_status 4 pl restricted Pandora.com - wybieraj, oceniaj i sluchaj tego co lubisz. Za free. Megasphaera true true rxpgnews.com true true 0 false all_ads 0 reddit.com archived meditation changes brain structure benm true true blogs.pragprog.com true true 0 false all_ads 7 programming public Annotate Models Plugin for Rails johnny_yuma true true cbsnews.com true false 1 false all_ads 9 reddit.com archived Kids Build Soybean-Fueled Car trost true true austin360.com true false 2 false all_ads 39 reddit.com archived Bah Hummer: Indie rockers reject big money from the king of gas guzzlers iwadon false true x.nest.jp true true 1 false no_status 0 ja public Life with Mac OS X @rNote - iCal、化けてませんか？ honekaimedia true true techeblog.com true false 0 false all_ads 1 reddit.com archived What if Microsoft Designed the iPod’s Packaging? dr2tom true true nightwithafuturist.com false true 1 false all_ads 0 reddit.com archived Future of Bio-Energy Event on March 6th bwmemail true true thisisbenslist.blogspot.com true true 0 false all_ads 0 reddit.com archived Neko Case Blacklisted dr2tom true true davinciinstitute.com false true 1 false all_ads 0 reddit.com archived Employee Retention Boot Camp on March 11th watanaa false true cqpub.co.jp true true 0 false no_status 4 ja public GCCの実行時に影響を及ぼす環境変数 iwadon false true cerlsoundgroup.org true true 1 false no_status 0 ja public Haken Audio jedberg true true redherring.com true true 0 false all_ads 0 reddit.com archived H&R Block Miscalculates Its Own Taxes mrstickman true true shipoffools.com true false 0 false all_ads 12 reddit.com archived Top 10 funny/offensive religious jokes [deleted] true false biologynews.net false true 0 false all_ads 0 reddit.com archived Bioengineers create stable networks of blood vessels watanaa false true geocities.jp true true 0 false no_status 0 ja public 博士（はくし）が100にんいるむら FiReaNG3L true true biologynews.net true false 1 false all_ads 3 reddit.com archived Predators keep the world green, ecologists find watanaa false true kmaebashi.com false true 0 false no_status 19 ja public プログラミング言語を作る watanaa false true pdos.csail.mit.edu true true 0 false no_status 4 ja public ランダムな計算機科学の論文を（グラフや図や引用付きで）作る [deleted] true false amasci.com false true 1 false all_ads 0 reddit.com archived "scratch holograms" -- make 3d images using grooves on a plastic surface tcox01 true true life.currenttoday.com false true 1 false all_ads 0 reddit.com archived No Time for Love tilto true true todaysthv.com true true 1 false all_ads 1 reddit.com archived Woman hires hitman to kill in order to steal cheese which she mistook for cocaine kvarko false true samopiniuloj.esperanto-jeunes.org true true 0 false no_status 4 eo public Samopiniuloj (cxiutaga retludo) jmuk false true alicia.zive.net true true 0 false no_status 0 ja public おおやにき: 調べろ。 maepon false true iwatam-server.dyndns.org true true 0 false no_status 9 ja public 議論のしかた raldi false true features.reddit.com true true 1 false no_status 0 features public Spend your time working on reddit: table infogami [deleted] true false en.w

In [22]:
df_train_p  = df_train.toPandas()

/databricks/spark/python/pyspark/sql/types.py:1636: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated, and in 3.8 it will stop working
 return pa.schema(fields)

In [23]:
from pyspark.ml.feature import RegexTokenizer

regexTokenizer = RegexTokenizer(gaps = False, pattern = '\w+', inputCol = 'domain', outputCol = 'domain_tok')

df_train = regexTokenizer.transform(df_train)
display(df_train)

author brand_safe can_gild domain is_crosspostable no_follow num_comments over_18 parent_whitelist_status score subreddit subreddit_type title domain_tok codepoet true true macgeekery.com true true 0 false all_ads 0 reddit.com archived Well That Was a Bust List(macgeekery, com) scylla true true msnbc.msn.com true true 0 false all_ads 0 reddit.com archived Holocaust: Why David Irving shouldn’t be jailed ( and it's not because he's in any ways right ) List(msnbc, msn, com) tilto true true iht.com true true 0 false all_ads 0 reddit.com archived Google shares fall sharply as CFO announces growth is slowing List(iht, com) Laibcoms true true gameshogun.info true true 0 false all_ads 0 reddit.com archived newsvine launching tomorrow! List(gameshogun, info) FaeLLe true true faelle.com true true 0 false all_ads 0 reddit.com archived VoodooPC to launch 8TB Media PC List(faelle, com) Megasphaera true true request.reddit.com true true 1 false all_ads 0 reddit.com archived kafka immigration List(request, reddit, com) alsaad false true pandora.com false true 0 false no_status 4 pl restricted Pandora.com - wybieraj, oceniaj i sluchaj tego co lubisz. Za free. List(pandora, com) Megasphaera true true rxpgnews.com true true 0 false all_ads 0 reddit.com archived meditation changes brain structure List(rxpgnews, com) benm true true blogs.pragprog.com true true 0 false all_ads 7 programming public Annotate Models Plugin for Rails List(blogs, pragprog, com) johnny_yuma true true cbsnews.com true false 1 false all_ads 9 reddit.com archived Kids Build Soybean-Fueled Car List(cbsnews, com) trost true true austin360.com true false 2 false all_ads 39 reddit.com archived Bah Hummer: Indie rockers reject big money from the king of gas guzzlers List(austin360, com) iwadon false true x.nest.jp true true 1 false no_status 0 ja public Life with Mac OS X @rNote - iCal、化けてませんか？ List(x, nest, jp) honekaimedia true true techeblog.com true false 0 false all_ads 1 reddit.com archived What if Microsoft Designed the iPod’s Packaging? List(techeblog, com) dr2tom true true nightwithafuturist.com false true 1 false all_ads 0 reddit.com archived Future of Bio-Energy Event on March 6th List(nightwithafuturist, com) bwmemail true true thisisbenslist.blogspot.com true true 0 false all_ads 0 reddit.com archived Neko Case Blacklisted List(thisisbenslist, blogspot, com) dr2tom true true davinciinstitute.com false true 1 false all_ads 0 reddit.com archived Employee Retention Boot Camp on March 11th List(davinciinstitute, com) watanaa false true cqpub.co.jp true true 0 false no_status 4 ja public GCCの実行時に影響を及ぼす環境変数 List(cqpub, co, jp) iwadon false true cerlsoundgroup.org true true 1 false no_status 0 ja public Haken Audio List(cerlsoundgroup, org) jedberg true true redherring.com true true 0 false all_ads 0 reddit.com archived H&R Block Miscalculates Its Own Taxes List(redherring, com) mrstickman true true shipoffools.com true false 0 false all_ads 12 reddit.com archived Top 10 funny/offensive religious jokes List(shipoffools, com) [deleted] true false biologynews.net false true 0 false all_ads 0 reddit.com archived Bioengineers create stable networks of blood vessels List(biologynews, net) watanaa false true geocities.jp true true 0 false no_status 0 ja public 博士（はくし）が100にんいるむら List(geocities, jp) FiReaNG3L true true biologynews.net true false 1 false all_ads 3 reddit.com archived Predators keep the world green, ecologists find List(biologynews, net) watanaa false true kmaebashi.com false true 0 false no_status 19 ja public プログラミング言語を作る List(kmaebashi, com) watanaa false true pdos.csail.mit.edu true true 0 false no_status 4 ja public ランダムな計算機科学の論文を（グラフや図や引用付きで）作る List(pdos, csail, mit, edu) [deleted] true false amasci.com false true 1 false all_ads 0 reddit.com archived "scratch holograms" -- make 3d images using grooves on a plastic surface List(amasci, com) tcox01 true true life.currenttoday.com false true 1 false all_ads 0 reddit.com archived No Time for Love List(life, curr

In [24]:
# remove stopwords
from pyspark.ml.feature import StopWordsRemover
swr = StopWordsRemover(inputCol = 'domain_tok', outputCol = 'domain_tok_sw')

df_train = swr.transform(df_train)
display(df_train)
# reviews_swr.write.saveAsTable('reviews_swr', mode = 'overwrite')

author brand_safe can_gild domain is_crosspostable no_follow num_comments over_18 parent_whitelist_status score subreddit subreddit_type title domain_tok domain_tok_sw codepoet true true macgeekery.com true true 0 false all_ads 0 reddit.com archived Well That Was a Bust List(macgeekery, com) List(macgeekery, com) scylla true true msnbc.msn.com true true 0 false all_ads 0 reddit.com archived Holocaust: Why David Irving shouldn’t be jailed ( and it's not because he's in any ways right ) List(msnbc, msn, com) List(msnbc, msn, com) tilto true true iht.com true true 0 false all_ads 0 reddit.com archived Google shares fall sharply as CFO announces growth is slowing List(iht, com) List(iht, com) Laibcoms true true gameshogun.info true true 0 false all_ads 0 reddit.com archived newsvine launching tomorrow! List(gameshogun, info) List(gameshogun, info) FaeLLe true true faelle.com true true 0 false all_ads 0 reddit.com archived VoodooPC to launch 8TB Media PC List(faelle, com) List(faelle, com) Megasphaera true true request.reddit.com true true 1 false all_ads 0 reddit.com archived kafka immigration List(request, reddit, com) List(request, reddit, com) alsaad false true pandora.com false true 0 false no_status 4 pl restricted Pandora.com - wybieraj, oceniaj i sluchaj tego co lubisz. Za free. List(pandora, com) List(pandora, com) Megasphaera true true rxpgnews.com true true 0 false all_ads 0 reddit.com archived meditation changes brain structure List(rxpgnews, com) List(rxpgnews, com) benm true true blogs.pragprog.com true true 0 false all_ads 7 programming public Annotate Models Plugin for Rails List(blogs, pragprog, com) List(blogs, pragprog, com) johnny_yuma true true cbsnews.com true false 1 false all_ads 9 reddit.com archived Kids Build Soybean-Fueled Car List(cbsnews, com) List(cbsnews, com) trost true true austin360.com true false 2 false all_ads 39 reddit.com archived Bah Hummer: Indie rockers reject big money from the king of gas guzzlers List(austin360, com) List(austin360, com) iwadon false true x.nest.jp true true 1 false no_status 0 ja public Life with Mac OS X @rNote - iCal、化けてませんか？ List(x, nest, jp) List(x, nest, jp) honekaimedia true true techeblog.com true false 0 false all_ads 1 reddit.com archived What if Microsoft Designed the iPod’s Packaging? List(techeblog, com) List(techeblog, com) dr2tom true true nightwithafuturist.com false true 1 false all_ads 0 reddit.com archived Future of Bio-Energy Event on March 6th List(nightwithafuturist, com) List(nightwithafuturist, com) bwmemail true true thisisbenslist.blogspot.com true true 0 false all_ads 0 reddit.com archived Neko Case Blacklisted List(thisisbenslist, blogspot, com) List(thisisbenslist, blogspot, com) dr2tom true true davinciinstitute.com false true 1 false all_ads 0 reddit.com archived Employee Retention Boot Camp on March 11th List(davinciinstitute, com) List(davinciinstitute, com) watanaa false true cqpub.co.jp true true 0 false no_status 4 ja public GCCの実行時に影響を及ぼす環境変数 List(cqpub, co, jp) List(cqpub, co, jp) iwadon false true cerlsoundgroup.org true true 1 false no_status 0 ja public Haken Audio List(cerlsoundgroup, org) List(cerlsoundgroup, org) jedberg true true redherring.com true true 0 false all_ads 0 reddit.com archived H&R Block Miscalculates Its Own Taxes List(redherring, com) List(redherring, com) mrstickman true true shipoffools.com true false 0 false all_ads 12 reddit.com archived Top 10 funny/offensive religious jokes List(shipoffools, com) List(shipoffools, com) [deleted] true false biologynews.net false true 0 false all_ads 0 reddit.com archived Bioengineers create stable networks of blood vessels List(biologynews, net) List(biologynews, net) watanaa false true geocities.jp true true 0 false no_status 0 ja public 博士（はくし）が100にんいるむら List(geocities, jp) List(geocities, jp) FiReaNG3L true true biologynews.net true false 1 false all_ads 3 reddit.com archived Predators keep the world green, ecologists find List(biologynews, net) List(biologynews, net) 

In [25]:
from pyspark.ml.feature import Word2Vec

#create an average word vector for each document (works well according to Zeyu & Shu)
word2vec = Word2Vec(vectorSize = 10, minCount = 5, inputCol = 'domain_tok_sw', outputCol = 'domain_tok_sw_w2v')
model = word2vec.fit(df_train)
df_train = model.transform(df_train)

# display(result)
df_train.show(1, truncate = True)

+--------+----------+--------+--------------+----------------+---------+------------+-------+-----------------------+-----+----------+--------------+--------------------+-----------------+-----------------+--------------------+
 author|brand_safe|can_gild| domain|is_crosspostable|no_follow|num_comments|over_18|parent_whitelist_status|score| subreddit|subreddit_type| title| domain_tok| domain_tok_sw| domain_tok_sw_w2v|
+--------+----------+--------+--------------+----------------+---------+------------+-------+-----------------------+-----+----------+--------------+--------------------+-----------------+-----------------+--------------------+
codepoet| true| true|macgeekery.com| true| true| 0| false| all_ads| 0|reddit.com| archived|Well That Was a Bust|[macgeekery, com]|[macgeekery, com]|[0.35445028543472...|
+--------+----------+--------+--------------+----------------+---------+------------+-------+-----------------------+-----+----------+--------------+--------------------+-----------------+-----------------+--------------------+
only showing top 1 row

In [26]:
regexTokenizer2 = RegexTokenizer(gaps = False, pattern = '\w+', inputCol = 'title', outputCol = 'title_tok')

df_train = regexTokenizer2.transform(df_train)

swr2 = StopWordsRemover(inputCol = 'title_tok', outputCol = 'title_tok_sw')

df_train = swr2.transform(df_train)

word2vec2 = Word2Vec(vectorSize = 10, minCount = 5, inputCol = 'title_tok_sw', outputCol = 'title_tok_sw_w2v')
model2 = word2vec2.fit(df_train)
df_train = model2.transform(df_train)

df_train.show(1)

<>:1: DeprecationWarning: invalid escape sequence \w
<>:1: DeprecationWarning: invalid escape sequence \w
<command-2527672591375366>:1: DeprecationWarning: invalid escape sequence \w
 regexTokenizer2 = RegexTokenizer(gaps = False, pattern = '\w+', inputCol = 'title', outputCol = 'title_tok')
+--------+----------+--------+--------------+----------------+---------+------------+-------+-----------------------+-----+----------+--------------+--------------------+-----------------+-----------------+--------------------+--------------------+------------+--------------------+
 author|brand_safe|can_gild| domain|is_crosspostable|no_follow|num_comments|over_18|parent_whitelist_status|score| subreddit|subreddit_type| title| domain_tok| domain_tok_sw| domain_tok_sw_w2v| title_tok|title_tok_sw| title_tok_sw_w2v|
+--------+----------+--------+--------------+----------------+---------+------------+-------+-----------------------+-----+----------+--------------+--------------------+-----------------+-----------------+--------------------+--------------------+------------+--------------------+
codepoet| true| true|macgeekery.com| true| true| 0| false| all_ads| 0|reddit.com| archived|Well That Was a Bust|[macgeekery, com]|[macgeekery, com]|[0.35445028543472...|[well, that, was,...|[well, bust]|[0.01580012403428...|
+--------+----------+--------+--------------+----------------+---------+------------+-------+-----------------------+-----+----------+--------------+--------------------+-----------------+-----------------+--------------------+--------------------+------------+--------------------+
only showing top 1 row

In [27]:
regexTokenizer_t = RegexTokenizer(gaps = False, pattern = '\w+', inputCol = 'title', outputCol = 'title_tok')

df_test = regexTokenizer_t.transform(df_test)

swr_t = StopWordsRemover(inputCol = 'title_tok', outputCol = 'title_tok_sw')

df_test = swr_t.transform(df_test)

word2vec_t = Word2Vec(vectorSize = 10, minCount = 5, inputCol = 'title_tok_sw', outputCol = 'title_tok_sw_w2v')
model_t = word2vec_t.fit(df_test)
df_test = model_t.transform(df_test)

df_test.show(1)

<>:1: DeprecationWarning: invalid escape sequence \w
<>:1: DeprecationWarning: invalid escape sequence \w
<command-2527672591375370>:1: DeprecationWarning: invalid escape sequence \w
 regexTokenizer_t = RegexTokenizer(gaps = False, pattern = '\w+', inputCol = 'title', outputCol = 'title_tok')
+------+----------+--------+--------------------+----------------+---------+------------+-------+-----------------------+-----+----------+--------------+--------------------+--------------------+--------------------+--------------------+
author|brand_safe|can_gild| domain|is_crosspostable|no_follow|num_comments|over_18|parent_whitelist_status|score| subreddit|subreddit_type| title| title_tok| title_tok_sw| title_tok_sw_w2v|
+------+----------+--------+--------------------+----------------+---------+------------+-------+-----------------------+-----+----------+--------------+--------------------+--------------------+--------------------+--------------------+
 spif| true| true|democrats.reform....| true| false| 0| false| all_ads| 4|reddit.com| archived|Iraq on the Recor...|[iraq, on, the, r...|[iraq, record, se...|[-0.0033969846864...|
+------+----------+--------+--------------------+----------------+---------+------------+-------+-----------------------+-----+----------+--------------+--------------------+--------------------+--------------------+--------------------+
only showing top 1 row

In [28]:
regexTokenizer_t2 = RegexTokenizer(gaps = False, pattern = '\w+', inputCol = 'domain', outputCol = 'domain_tok')

df_test = regexTokenizer_t2.transform(df_test)

swr_t2 = StopWordsRemover(inputCol = 'domain_tok', outputCol = 'domain_tok_sw')

df_test = swr_t2.transform(df_test)

word2vec_t2 = Word2Vec(vectorSize = 10, minCount = 5, inputCol = 'domain_tok_sw', outputCol = 'domain_tok_sw_w2v')
model_t2 = word2vec_t2.fit(df_test)
df_test = model_t2.transform(df_test)

df_test.show(1)

<>:1: DeprecationWarning: invalid escape sequence \w
<>:1: DeprecationWarning: invalid escape sequence \w
<command-2527672591375371>:1: DeprecationWarning: invalid escape sequence \w
 regexTokenizer_t2 = RegexTokenizer(gaps = False, pattern = '\w+', inputCol = 'domain', outputCol = 'domain_tok')
+------+----------+--------+--------------------+----------------+---------+------------+-------+-----------------------+-----+----------+--------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
author|brand_safe|can_gild| domain|is_crosspostable|no_follow|num_comments|over_18|parent_whitelist_status|score| subreddit|subreddit_type| title| title_tok| title_tok_sw| title_tok_sw_w2v| domain_tok| domain_tok_sw| domain_tok_sw_w2v|
+------+----------+--------+--------------------+----------------+---------+------------+-------+-----------------------+-----+----------+--------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
 spif| true| true|democrats.reform....| true| false| 0| false| all_ads| 4|reddit.com| archived|Iraq on the Recor...|[iraq, on, the, r...|[iraq, record, se...|[-0.0033969846864...|[democrats, refor...|[democrats, refor...|[0.01163703203201...|
+------+----------+--------+--------------------+----------------+---------+------------+-------+-----------------------+-----+----------+--------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
only showing top 1 row

In [29]:
df_train.columns

Out[27]: ['author',
 'brand_safe',
 'can_gild',
 'domain',
 'is_crosspostable',
 'no_follow',
 'num_comments',
 'over_18',
 'parent_whitelist_status',
 'score',
 'subreddit',
 'subreddit_type',
 'title',
 'domain_tok',
 'domain_tok_sw',
 'domain_tok_sw_w2v',
 'title_tok',
 'title_tok_sw',
 'title_tok_sw_w2v']

In [30]:
columns_to_drop = ['author', 'domain', 'title', 'domain_tok', 'domain_tok_sw', 'title_tok', 'title_tok_sw']

df_train = df_train.drop(*columns_to_drop)
df_test = df_test.drop(*columns_to_drop)

In [31]:
len(df_train.columns), len(df_test.columns)

Out[29]: (12, 12)

In [32]:
from pyspark.ml.feature import VectorAssembler
vectorAssembler = VectorAssembler(inputCols = ['brand_safe', 'can_gild', 'is_crosspostable', 'no_follow', 'over_18', \
                                     'domain_tok_sw_w2v', 'title_tok_sw_w2v'], outputCol = 'features')
df_t = vectorAssembler.transform(df_train)
df_t = df_t.select(['features', 'score'])
df_t.show(3)

+--------------------+-----+
 features|score|
+--------------------+-----+
[1.0,1.0,1.0,1.0,...| 0|
[1.0,1.0,1.0,1.0,...| 0|
[1.0,1.0,1.0,1.0,...| 0|
+--------------------+-----+
only showing top 3 rows

In [33]:
vectorAssembler_t = VectorAssembler(inputCols = ['brand_safe', 'can_gild', 'is_crosspostable', 'no_follow', 'over_18', \
                                     'domain_tok_sw_w2v', 'title_tok_sw_w2v'], outputCol = 'features')
df_t2 = vectorAssembler_t.transform(df_test)
df_t2 = df_t2.select(['features', 'score'])
df_t2.show(3)

+--------------------+-----+
 features|score|
+--------------------+-----+
[1.0,1.0,1.0,0.0,...| 4|
[0.0,1.0,1.0,0.0,...| 3|
[1.0,1.0,0.0,1.0,...| 0|
+--------------------+-----+
only showing top 3 rows

In [34]:
display(df_t)

features score List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.3544502854347229, -0.6449003219604492, -0.4270171523094177, -0.1300344318151474, 0.3328089118003845, 0.1513465791940689, 0.051165349781513214, -0.40864062309265137, 0.07422507554292679, 0.45328983664512634, 0.015800124034285545, 0.02123221382498741, -0.0022580502554774284, -0.0097417663782835, -0.005755799822509289, -0.004218887072056532, -0.0067719086073338985, -0.01841377653181553, -0.01630293019115925, 0.018032256513834)) 0 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.2198091975102822, -0.5566953718662262, -0.37900424997011817, 0.1516778568426768, 0.31289644042650855, 0.08059688284993172, 0.19617316623528797, -0.19998193780581155, 0.05908615266283353, 0.29586882392565406, -0.005773128675562994, -0.012588509391727192, -0.020303547249308652, 0.005543550609477929, 0.019453893615198985, 0.00971975816147668, -0.011488526003501776, -0.01310856786689588, -0.002863977603348238, -0.004415305863533701)) 0 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.2916935980319977, -0.6049031801521778, -0.42878722690511495, -0.0017236322164535522, 0.3289696762803942, 0.21810894459486008, 0.12646116316318512, -0.40581999509595335, -0.0017805993556976318, 0.4422566844150424, 0.02898435399401933, 0.010768831241875887, -0.0532741661882028, 0.007837481563910842, 0.019248876080382615, 0.03130364022217691, -0.0042136122938245535, 0.008642591070383787, 0.0025228934828191996, 0.005627083010040224)) 0 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.06950278207659721, -0.09616354992613196, -0.2503345283330418, -0.2301531843841076, -0.0982899647206068, 0.054081156849861145, -0.13172189984470606, 0.06605144450441003, 0.14204961759969592, -0.02052687481045723, 0.010734148944417635, -0.0021840371191501617, -0.024106156080961227, 0.00799249392002821, 0.027912658949693043, -0.016466011914114155, 0.024089742451906204, -0.02044922610123952, 0.004474412960310777, 0.020337664832671482)) 0 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.3544502854347229, -0.6449003219604492, -0.4270171523094177, -0.1300344318151474, 0.3328089118003845, 0.1513465791940689, 0.051165349781513214, -0.40864062309265137, 0.07422507554292679, 0.45328983664512634, 0.004096581041812897, -0.010167287569493056, -0.01658760318532586, 0.011622516810894013, 0.01980698322877288, 0.006437075883150101, -0.004793687164783478, 0.01516856998205185, -0.016549307480454446, -0.0012607873417437077)) 0 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.2870828260978063, -0.49103987713654834, -0.38307138284047443, 0.012741322939594586, 0.4146902107944091, 0.2853822310765584, 0.12415572566290696, -0.3079897020943463, -0.06019148230552673, 0.41112400839726126, 0.004198136273771524, -0.012488183565437794, -0.03997119516134262, 0.010088421404361725, 0.023168547078967094, -0.011859181337058544, 0.008104964159429073, 3.9321655640378594E-4, -0.012698360718786716, 0.02314193919301033)) 0 List(1, 25, List(), List(0.0, 1.0, 0.0, 1.0, 0.0, 0.3544502854347229, -0.6449003219604492, -0.4270171523094177, -0.1300344318151474, 0.3328089118003845, 0.1513465791940689, 0.051165349781513214, -0.40864062309265137, 0.07422507554292679, 0.45328983664512634, -0.011909103766083718, 0.003631064482033253, -0.005362836667336524, 0.025806966796517374, 0.029012725688517094, 0.004187270998954773, 0.003417332749813795, 0.009690045076422394, -0.0020867966115474704, -6.760217249393464E-4)) 4 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.3544502854347229, -0.6449003219604492, -0.4270171523094177, -0.1300344318151474, 0.3328089118003845, 0.1513465791940689, 0.051165349781513214, -0.40864062309265137, 0.07422507554292679, 0.45328983664512634, 0.035641176626086235, 0.001686709700152278, -0.033007376827299595, 0.012626323034055531, 0.024362491676583886, -0.012495958944782615, 0.019322329200804234, 0.034846687223762274, 0.015529385767877102, 0.011660400894470513)) 0 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.39519235491752625, -0.5173403024673462, -

In [35]:
from pyspark.ml.regression import LinearRegression
lr = LinearRegression(featuresCol = 'features', labelCol='score', maxIter=1000, regParam=0.3, elasticNetParam=0.8)
lr_model = lr.fit(df_t)
print("Coefficients: " + str(lr_model.coefficients))
print("Intercept: " + str(lr_model.intercept))

Coefficients: [2.0847264689837854,0.0,0.8046469436538374,-28.63381901047469,2.798282401516842,1.4665606909319806,0.0,0.0,0.0,0.0,1.5406183097522614,0.0,0.0,0.0,2.4680963476975672,0.0,0.0,-1.8584448975368324,0.0,0.0,0.0,0.0,0.0,-13.243593727812343,0.0]
Intercept: 26.433913934965563

In [36]:
trainingSummary = lr_model.summary
print("RMSE: %f" % trainingSummary.rootMeanSquaredError)
print("r2: %f" % trainingSummary.r2)

RMSE: 26.478429
r2: 0.172219

In [37]:
lr_predictions = lr_model.transform(df_t2)
lr_predictions.select("prediction","score","features").show(5)
from pyspark.ml.evaluation import RegressionEvaluator
lr_evaluator = RegressionEvaluator(predictionCol="prediction", \
                 labelCol="score",metricName="r2")
print("R Squared (R2) on test data = %g" % lr_evaluator.evaluate(lr_predictions))

+------------------+-----+--------------------+
 prediction|score| features|
+------------------+-----+--------------------+
29.365763949058227| 4|[1.0,1.0,1.0,0.0,...|
28.843163766256573| 3|[0.0,1.0,1.0,0.0,...|
0.9414036366733889| 0|[1.0,1.0,0.0,1.0,...|
 30.61118659548501| 3|[1.0,1.0,1.0,0.0,...|
2.0776960852079043| 0|[0.0,1.0,0.0,1.0,...|
+------------------+-----+--------------------+
only showing top 5 rows

R Squared (R2) on test data = 0.181522

In [38]:
test_result = lr_model.evaluate(df_t2)
print("Root Mean Squared Error (RMSE) on test data = %g" % test_result.rootMeanSquaredError)

Root Mean Squared Error (RMSE) on test data = 26.5445

In [39]:
print("numIterations: %d" % trainingSummary.totalIterations)
print("objectiveHistory: %s" % str(trainingSummary.objectiveHistory))
trainingSummary.residuals.show()

numIterations: 31
objectiveHistory: [0.4999999999999999, 0.48107291079931275, 0.4203988718540605, 0.41984702571242377, 0.41865016878253214, 0.41846861027027155, 0.418210426130459, 0.4181907668375514, 0.4181881703986842, 0.4181872380706913, 0.41818621146494456, 0.4181853867668939, 0.4181851522283877, 0.4181849993550169, 0.4181848273380446, 0.4181847664938626, 0.4181847548225021, 0.4181847536976898, 0.4181847516409233, 0.41818475148393214, 0.41818475140187766, 0.418184751305095, 0.4181847512686384, 0.41818475124678717, 0.4181847512430317, 0.4181847512381702, 0.4181847512360244, 0.41818475123435095, 0.41818475123387117, 0.41818475123385285, 0.4181847512337699]
+-------------------+
 residuals|
+-------------------+
-2.7813273399339735|
-1.9418960424700984|
 -2.610404368929917|
-0.8095971562896693|
 -2.811220945183617|
 -2.807307673040633|
 4.290548695747276|
-2.4168990090272366|
 3.971503937134603|
-22.278173586705783|
 7.708588938860533|
 1.6176415662445685|
 -30.08606638141741|
-1.9844387186496135|
 -2.582243150615458|
-1.8898667694729419|
 5.383059966871226|
-0.3200097579665453|
 -2.834709451101233|
-19.326911944757796|
+-------------------+
only showing top 20 rows

In [40]:
display(df_t)

features score List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.3544502854347229, -0.6449003219604492, -0.4270171523094177, -0.1300344318151474, 0.3328089118003845, 0.1513465791940689, 0.051165349781513214, -0.40864062309265137, 0.07422507554292679, 0.45328983664512634, 0.015800124034285545, 0.02123221382498741, -0.0022580502554774284, -0.0097417663782835, -0.005755799822509289, -0.004218887072056532, -0.0067719086073338985, -0.01841377653181553, -0.01630293019115925, 0.018032256513834)) 0 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.2198091975102822, -0.5566953718662262, -0.37900424997011817, 0.1516778568426768, 0.31289644042650855, 0.08059688284993172, 0.19617316623528797, -0.19998193780581155, 0.05908615266283353, 0.29586882392565406, -0.005773128675562994, -0.012588509391727192, -0.020303547249308652, 0.005543550609477929, 0.019453893615198985, 0.00971975816147668, -0.011488526003501776, -0.01310856786689588, -0.002863977603348238, -0.004415305863533701)) 0 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.2916935980319977, -0.6049031801521778, -0.42878722690511495, -0.0017236322164535522, 0.3289696762803942, 0.21810894459486008, 0.12646116316318512, -0.40581999509595335, -0.0017805993556976318, 0.4422566844150424, 0.02898435399401933, 0.010768831241875887, -0.0532741661882028, 0.007837481563910842, 0.019248876080382615, 0.03130364022217691, -0.0042136122938245535, 0.008642591070383787, 0.0025228934828191996, 0.005627083010040224)) 0 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.06950278207659721, -0.09616354992613196, -0.2503345283330418, -0.2301531843841076, -0.0982899647206068, 0.054081156849861145, -0.13172189984470606, 0.06605144450441003, 0.14204961759969592, -0.02052687481045723, 0.010734148944417635, -0.0021840371191501617, -0.024106156080961227, 0.00799249392002821, 0.027912658949693043, -0.016466011914114155, 0.024089742451906204, -0.02044922610123952, 0.004474412960310777, 0.020337664832671482)) 0 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.3544502854347229, -0.6449003219604492, -0.4270171523094177, -0.1300344318151474, 0.3328089118003845, 0.1513465791940689, 0.051165349781513214, -0.40864062309265137, 0.07422507554292679, 0.45328983664512634, 0.004096581041812897, -0.010167287569493056, -0.01658760318532586, 0.011622516810894013, 0.01980698322877288, 0.006437075883150101, -0.004793687164783478, 0.01516856998205185, -0.016549307480454446, -0.0012607873417437077)) 0 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.2870828260978063, -0.49103987713654834, -0.38307138284047443, 0.012741322939594586, 0.4146902107944091, 0.2853822310765584, 0.12415572566290696, -0.3079897020943463, -0.06019148230552673, 0.41112400839726126, 0.004198136273771524, -0.012488183565437794, -0.03997119516134262, 0.010088421404361725, 0.023168547078967094, -0.011859181337058544, 0.008104964159429073, 3.9321655640378594E-4, -0.012698360718786716, 0.02314193919301033)) 0 List(1, 25, List(), List(0.0, 1.0, 0.0, 1.0, 0.0, 0.3544502854347229, -0.6449003219604492, -0.4270171523094177, -0.1300344318151474, 0.3328089118003845, 0.1513465791940689, 0.051165349781513214, -0.40864062309265137, 0.07422507554292679, 0.45328983664512634, -0.011909103766083718, 0.003631064482033253, -0.005362836667336524, 0.025806966796517374, 0.029012725688517094, 0.004187270998954773, 0.003417332749813795, 0.009690045076422394, -0.0020867966115474704, -6.760217249393464E-4)) 4 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.3544502854347229, -0.6449003219604492, -0.4270171523094177, -0.1300344318151474, 0.3328089118003845, 0.1513465791940689, 0.051165349781513214, -0.40864062309265137, 0.07422507554292679, 0.45328983664512634, 0.035641176626086235, 0.001686709700152278, -0.033007376827299595, 0.012626323034055531, 0.024362491676583886, -0.012495958944782615, 0.019322329200804234, 0.034846687223762274, 0.015529385767877102, 0.011660400894470513)) 0 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.39519235491752625, -0.5173403024673462, -

In [41]:
from pyspark.ml.regression import RandomForestRegressor

rf = RandomForestRegressor(labelCol="score", featuresCol="features")

rf_model = rf.fit(df_t)

predictions = rf_model.transform(df_t2)

In [42]:
display(predictions)

features score prediction List(1, 25, List(), List(1.0, 1.0, 1.0, 0.0, 0.0, 0.01163703203201294, 0.018528031185269356, -4.7532934695482254E-4, -0.009292944334447384, 0.0027298512868583202, -0.002496141940355301, 0.018059439957141876, -0.001220962032675743, 0.016040101647377014, -0.0054797520861029625, -0.003396984686454137, 0.003152846141407887, -0.0321441267306606, 0.004761212412267924, 0.039769863872788844, -0.001328083345045646, -0.036600311286747456, 0.026752047209690013, 0.0012804487099250157, 0.02216167648633321)) 4 20.08248928226738 List(1, 25, List(), List(0.0, 1.0, 1.0, 0.0, 0.0, 0.24950194358825684, -0.020930277183651924, -0.18183720111846924, 0.2022489756345749, 0.4538852572441101, 0.5643795728683472, 0.08349420875310898, -0.4040583372116089, 0.01895042695105076, 0.1168494001030922, -0.008581571280956268, -0.020775021364291508, -0.016004205991824467, -0.01982708399494489, 0.009235601251324017, -0.0043544284999370575, -0.013786935557921726, -0.001233439582089583, -0.0038555342083175974, 0.0010204976424574852)) 3 15.1222670285436 List(1, 25, List(), List(1.0, 1.0, 0.0, 1.0, 0.0, 0.21803046762943268, -0.47431802842766047, -0.23690887726843357, -0.3911142647266388, -0.0011392831802368164, -0.18379954807460308, -0.4019920900464058, -0.058268796652555466, 0.030791383236646652, 0.3372248634696007, -0.027211878759165604, -0.021771760036547978, 0.021709407369295754, 0.009049680549651384, -0.010956250752011934, -0.018087375909090042, 0.004524710277716318, -0.0022423543656865754, -0.017218480662753183, -0.006941353591779867)) 0 2.3844394549792263 List(1, 25, List(), List(1.0, 1.0, 1.0, 0.0, 0.0, 0.1663346290588379, -0.013953518122434616, -0.12122480074564615, 0.13483265042304993, 0.30259017149607337, 0.3762530485788981, 0.05566280583540598, -0.26937222480773926, 0.012633617967367172, 0.07789960006872812, -0.011931269119183222, 0.0015300199932729204, -0.013037876846889654, -0.00404514092952013, 0.02305790999283393, 0.008133221107224623, -0.02081382346417134, 0.05468489117144296, -0.018711174217363197, 0.019643416240190465)) 3 32.93097371301068 List(1, 25, List(), List(0.0, 1.0, 0.0, 1.0, 1.0, 0.21803046762943268, -0.47431802842766047, -0.23690887726843357, -0.3911142647266388, -0.0011392831802368164, -0.18379954807460308, -0.4019920900464058, -0.058268796652555466, 0.030791383236646652, 0.3372248634696007, -0.027671108953654766, 0.04154927562922239, -0.006094903685152531, 0.008473582391161472, 0.03164350055158138, -0.009911970002576709, -0.00785964378155768, 0.02851010113954544, -0.04523683758452535, -0.00813448615372181)) 0 5.990642618562214 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.0748219033703208, -0.3186250440776348, 0.16949260979890823, 0.7122031012549996, 0.21246505063027143, -0.08737022802233696, 0.05481266789138317, -0.13604910671710968, -0.19225259870290756, 0.4397807791829109, -0.0033313754746424297, 0.0196296785558973, -0.006119988858699799, 0.0072330671495624945, -0.01083363898630653, 0.018903604708611965, -0.014160561375319958, 0.016897618837122406, -0.0018269295022556823, -0.010999935013907296)) 0 1.367696013102703 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.11850496381521225, -0.4273155555129051, -0.23479899143179256, -0.20534645020961761, 0.060374402130643524, -0.012763197223345438, -0.3107160006960233, -0.060718162606159844, 0.0441765886110564, 0.26457426076134044, -0.006829228795443972, 0.029722367723782856, -0.035174701983729996, 0.039567273731033005, 0.03718594298698008, 0.002982049365527928, -0.030011071357876062, 0.03070251845444242, -0.004444971952276925, 0.017960386894022424)) 0 1.4685143046567335 List(1, 25, List(), List(1.0, 1.0, 1.0, 1.0, 0.0, 0.15742982923984528, -0.500049801543355, -0.29093921929597855, -0.3333391025662422, -0.15160523355007172, -0.09974243491888046, -0.4233591668307781, 0.04152049869298935, 0.00580219179391861, 0.3258182182908058, -0.03073304444551468, 0.04304679520428181, -0.034380271285772326, 0.009451311454176903, 0.07352487542666496, 0.0042274782434105875, 0.

In [43]:
import mlflow
from pyspark.ml import Pipeline

pipeline = Pipeline(stages=[rf])

from pyspark.ml.tuning import CrossValidator
from pyspark.ml.evaluation import RegressionEvaluator

from pyspark.ml.tuning import ParamGridBuilder
import numpy as np

paramGrid = ParamGridBuilder() \
    .addGrid(rf.numTrees, [int(x) for x in np.linspace(start = 10, stop = 50, num = 3)]) \
    .addGrid(rf.maxDepth, [int(x) for x in np.linspace(start = 5, stop = 25, num = 3)]) \
    .build()

crossval = CrossValidator(estimator=pipeline,
                          estimatorParamMaps=paramGrid,
                          evaluator=RegressionEvaluator(),
                          numFolds=3)

cvModel = crossval.fit(df_t)

predictions = cvModel.transform(df_t2)

--------------------------------------------------------------------------- 
 Py4JJavaError Traceback (most recent call last)
 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 62 try : 
 ---> 63 return f ( * a , ** kw ) 
 64 except py4j . protocol . Py4JJavaError as e : 

 /databricks/spark/python/lib/py4j-0.10.7-src.zip/py4j/protocol.py in get_return_value (answer, gateway_client, target_id, name) 
 327 "An error occurred while calling {0}{1}{2}.\n" . 
 --> 328 format(target_id, ".", name), value)
 329 else : 

 Py4JJavaError : An error occurred while calling o3169.evaluate.
: java.lang.IllegalArgumentException: Field "label" does not exist.
Available fields: features, score, CrossValidator_5be749d5a4f4_rand, prediction
	at org.apache.spark.sql.types.StructType$$anonfun$apply$1.apply(StructType.scala:274)
	at org.apache.spark.sql.types.StructType$$anonfun$apply$1.apply(StructType.scala:274)
	at scala.collection.MapLike$class.getOrElse(MapLike.scala:128)
	at scala.collection.AbstractMap.getOrElse(Map.scala:59)
	at org.apache.spark.sql.types.StructType.apply(StructType.scala:273)
	at org.apache.spark.ml.util.SchemaUtils$.checkNumericType(SchemaUtils.scala:74)
	at org.apache.spark.ml.evaluation.RegressionEvaluator.evaluate(RegressionEvaluator.scala:78)
	at sun.reflect.NativeMethodAccessorImpl.invoke0(Native Method)
	at sun.reflect.NativeMethodAccessorImpl.invoke(NativeMethodAccessorImpl.java:62)
	at sun.reflect.DelegatingMethodAccessorImpl.invoke(DelegatingMethodAccessorImpl.java:43)
	at java.lang.reflect.Method.invoke(Method.java:498)
	at py4j.reflection.MethodInvoker.invoke(MethodInvoker.java:244)
	at py4j.reflection.ReflectionEngine.invoke(ReflectionEngine.java:380)
	at py4j.Gateway.invoke(Gateway.java:295)
	at py4j.commands.AbstractCommand.invokeMethod(AbstractCommand.java:132)
	at py4j.commands.CallCommand.execute(CallCommand.java:79)
	at py4j.GatewayConnection.run(GatewayConnection.java:251)
	at java.lang.Thread.run(Thread.java:748)


During handling of the above exception, another exception occurred:

 IllegalArgumentException Traceback (most recent call last)
 <command-2527672591375388> in <module> 
 20 numFolds=3)
 21 
 ---> 22 cvModel = crossval . fit ( df_t ) 
 23 
 24 predictions = cvModel . transform ( df_t2 ) 

 /databricks/spark/python/pyspark/ml/base.py in fit (self, dataset, params) 
 130 return self . copy ( params ) . _fit ( dataset ) 
 131 else : 
 --> 132 return self . _fit ( dataset ) 
 133 else : 
 134 raise ValueError("Params must be either a param map or a list/tuple of param maps, "

 /databricks/spark/python/pyspark/ml/tuning.py in _fit (self, dataset) 
 308 
 309 tasks = _parallelFitTasks ( est , train , eva , validation , epm , collectSubModelsParam ) 
 --> 310 for j , metric , subModel in pool . imap_unordered ( lambda f : f ( ) , tasks ) : 
 311 metrics [ j ] += ( metric / nFolds ) 
 312 metrics_all [ i ] [ j ] = metric

 /usr/lib/python3.7/multiprocessing/pool.py in next (self, timeout) 
 746 if success : 
 747 return value
 --> 748 raise value
 749 
 750 __next__ = next # XXX 

 /usr/lib/python3.7/multiprocessing/pool.py in worker (inqueue, outqueue, initializer, initargs, maxtasks, wrap_exception) 
 119 job , i , func , args , kwds = task
 120 try : 
 --> 121 result = ( True , func ( * args , ** kwds ) ) 
 122 except Exception as e : 
 123 if wrap_exception and func is not _helper_reraises_exception : 

 /databricks/spark/python/pyspark/ml/tuning.py in <lambda> (f) 
 308 
 309 tasks = _parallelFitTasks ( est , train , eva , validation , epm , collectSubModelsParam ) 
 --> 310 for j , metric , subModel in pool . imap_unordered ( lambda f : f ( ) , tasks ) : 
 311 metrics [ j ] += ( metric / nFolds ) 
 312 metrics_all [ i ] [ j ] = metric

 /databricks/spark/python/pyspark/ml/tuning.py in singleTask () 
 53 def singleTask ( ) : 
 54 index , model = next ( modelIter ) 
 ---> 55 metric = eva . evaluate ( model . transform ( validation , epm [ index ] ) ) 
 56 return index , metric 

In [44]:
import matplotlib.pyplot as plt

evaluator = RegressionEvaluator(labelCol="score", predictionCol="prediction", metricName="rmse")

rmse = evaluator.evaluate(predictions)

rfPred = cvModel.transform(df)

rfResult = rfPred.toPandas()

plt.plot(rfResult.label, rfResult.prediction, 'bo')
plt.xlabel('Price')
plt.ylabel('Prediction')
plt.suptitle("Model Performance RMSE: %f" % rmse)
plt.show()

In [45]:
display(df_train)

In [46]:
import seaborn as sns

sns.boxplot("score", data=df_train_p[df_train_p["score"]<=200])

In [47]:
display(df_train.select("*").where(df_train.score <= 200))

In [48]:
df_train_num = df_train.select("brand_safe", "can_gild", "is_crosspostable", "num_comments", "no_follow", "over_18",  "score")
display(df_train_num)

In [49]:
display(features.collect())

In [50]:
features = df_train_num.rdd.map(lambda row: row[0:])

from pyspark.mllib.stat import Statistics

corr_mat=Statistics.corr(features, method="pearson")

In [51]:
print(corr_mat)

In [52]:
from pyspark.ml.stat import Correlation
from pyspark.ml.feature import VectorAssembler

# convert to vector column first
vector_col = "score"
assembler = VectorAssembler(inputCols=df_train_num.columns, outputCol=vector_col)
df_vector = assembler.transform(df_train_num).select(vector_col)

# get correlation matrix
matrix = Correlation.corr(df_vector, vector_col)

In [53]:
import numpy as np
import matplotlib.pyplot as plt

In [54]:
var = 'score'
x = df_train[var].values
bins = np.arange(0, 100, 5.0)

plt.figure(figsize=(10,8))
# the histogram of the data
plt.hist(x, bins, alpha=0.8, histtype='bar', color='gold',
         ec='black',weights=np.zeros_like(x) + 100. / x.size)

plt.xlabel(var)
plt.ylabel('percentage')
plt.xticks(bins)
plt.show()

In [55]:
df_train["score"].values

In [56]:
%sql

/* Query the created temp table in a SQL cell */

select * from `RS_v2_2006_03`

In [57]:
# With this registered as a temp view, it will only be available to this particular notebook. If you'd like other users to be able to query this table, you can also create a table from the DataFrame.
# Once saved, this table will persist across cluster restarts as well as allow various users across different notebooks to query this data.
# To do so, choose your table name and uncomment the bottom line.

permanent_table_name = "RS_v2_2006_03"

# df.write.format("parquet").saveAsTable(permanent_table_name)